Université Paul Sabatier

EIMAB3H1 - Analyse et exploitation de données

Enseignant : **José G. Moreno**

## TP 3. Extraction d'information sur des documents textuels (3/3)
IV - L'extraction d'information sur des documents semi-structurés
Wikipédia s'autodécrit comme « une encyclopédie alimentée sur internet par des volontaires.
Universelle, multilingue et fonctionnant sur le principe du wiki, chacun peut y collaborer
immédiatement. Wikipédia a pour objectif d'offrir un contenu libre, objectif et vérifiable que chacun
peut modifier et améliorer, sans nécessité de s'enregistrer. Tous les articles de Wikipédia sont un travail
en progression qui peut être modifié et amélioré par tout le monde ».
Pour tant Wikipédia est une ressource volatile, mais qui contient (au peut contenir) des informations
vérifiées par des tiers. Par exemple, pour connaître le vainqueur de la coupe du monde en 2014, il suffit
de regarder la page Wikipédia [ 2014 FIFA World Cup](https://simple.wikipedia.org/wiki/2014_FIFA_World_Cup) et lire dans l’info-box l'information du
vainqueur.
Voici le débout du contenu de la balise « text » qui est contenue dans un balise « page » qui a comme
titre « 2014 FIFA World Cup » (cette information
a été obtenue comme dans le TP 1 et TP 2). 

In [ ]:
!wget https://dumps.wikimedia.org/simplewiki/20200901/simplewiki-20200901-pages-articles.xml.bz2
!bzip2 -d simplewiki-20200901-pages-articles.xml.bz2
! echo "<mediawiki>" > simplewiki-20200901-pages-articles.xml.clean
! tail -n +2 simplewiki-20200901-pages-articles.xml >> simplewiki-20200901-pages-articles.xml.clean

--2020-11-08 16:31:52--  https://dumps.wikimedia.org/simplewiki/20200901/simplewiki-20200901-pages-articles.xml.bz2
Resolving dumps.wikimedia.org (dumps.wikimedia.org)... 208.80.154.7, 2620:0:861:1:208:80:154:7
Connecting to dumps.wikimedia.org (dumps.wikimedia.org)|208.80.154.7|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 179777498 (171M) [application/octet-stream]
Saving to: ‘simplewiki-20200901-pages-articles.xml.bz2.1’

simplewiki-20200901 100%[===================>] 171.45M  4.79MB/s    in 35s     

2020-11-08 16:32:28 (4.84 MB/s) - ‘simplewiki-20200901-pages-articles.xml.bz2.1’ saved [179777498/179777498]

bzip2: Output file simplewiki-20200901-pages-articles.xml already exists.


In [ ]:
#Title 
import pandas as pd
import xml.etree.ElementTree as et

def parse_XML(xml_file, df_cols): 
    """Parse the input XML file and store the result in a pandas 
    DataFrame with the given columns. 
    
    The first element of df_cols is supposed to be the identifier 
    variable, which is an attribute of each node element in the 
    XML data; other features will be parsed from the text content 
    of each sub-element. 
    """
    
    xtree = et.parse(xml_file)
    xroot = xtree.getroot()
    rows = []
    
    for node in xroot: 
        if node.find(df_cols[0]) is not None:
            res = [node.find(df_cols[0]).text]
            for el in df_cols[1:]: 
                if node is not None and node.find('revision',).find(el,) is not None:
                    res.append(node.find('revision',).find(el).text)
                else: 
                    res.append(None)
            rows.append({df_cols[i]: res[i] 
                     for i, _ in enumerate(df_cols)})
    
    out_df = pd.DataFrame(rows, columns=df_cols)
        
    return out_df

In [ ]:
df = parse_XML("simplewiki-20200901-pages-articles.xml.clean", ["title", "text"])
df

title                                               text
0                            April  {{monththisyear|4}}\n'''April''' is the fourth...
1                           August  {{monththisyear|8}}\n'''August''' (Aug.) is th...
2                              Art  [[Category:Art| ]]\n[[Category:Non-verbal comm...
3                                A  {{about| the first [[letter]] in the [[alphabe...
4                              Air  {{Simplify|date=February 2020}}\n[[Image:Kawas...
...                            ...                                                ...
319768  Workers and Peasants Party  Bhagat sing was the grastest Second freedom fi...
319769          Vladislav Krapivin  [[File:Krapivin 2006.jpg|right|200px]]\n'''Vla...
319770                Tomomi Inada  {{Infobox officeholder\n|name           = Tomo...
319771              Shigeru Ishiba  {{Infobox officeholder\n|name           = Shig...
319772              The Comey Rule  {{italictitle}}\n'''''The Comey Rule''''' is a...

[319773 rows x 2 columns]

In [ ]:
# voci le code si vous voulez visualizer que 2000 exemples (cette visualization est limité à 20000 éléments)
from google.colab import data_table
data_table.DataTable(df.sample(2000), include_index=False, num_rows_per_page=10)

Nous allons accéder à la page  Wikipédia « 2014 FIFA World Cup » :

In [ ]:
print(df[df['title']=='2014 FIFA World Cup']['text'].values)

['{{Infobox International Football Competition\n| tourney_name = FIFA World Cup\n| year = 2014\n| other_titles   = Copa do Mundo da FIFA<br />Brasil 2014{{refn|group=nb|The [[Portuguese language|Portuguese]] pronunciation is {{IPA-pt|ˈkɔpɐ du ˈmũdu dɐ ˈfifɐ bɾɐˈziw ˈdojz ˈmiw i kɐˈtoʁzi|}}, in Brazil\'s standard pronunciation.}}\n| image = Philipp Lahm lifts the 2014 FIFA World Cup.jpg\n| size = 250px\n| caption = Germany lifting the World Cup trophy.\n| country = Brazil\n| dates = 13 June – 13 July\n| confederations = 6\n| num_teams = 32\n| venues = 12\n| cities = 12\n| champion = Germany\n| count = 4\n| second = Argentina\n| third = Netherlands\n| fourth = Brazil\n| matches = 64\n| goals = 171\n| attendance = 3429873\n| top_scorer = {{flagicon|Colombia}} [[James Rodríguez]]<ref>{{cite web|url=http://www.bbc.com/sport/football/world-cup/top-scorers|title=Top Scorers - World Cup - Football|website=BBC Sport}}</ref><br>(6 goals)\n| prevseason = [[2010 FIFA World Cup|2010]]\n| nextseason

In [ ]:
def getInfobox(text):
    flag = [False, 0]
    res = ''
    for line in text.split('\n'):
        if '{{Infobox' in line:
            flag = [True,1]
        if flag[0]:
            res += line+'\n'
        if '}}' == line[:2]:
            flag = [False,0]
    return res

In [ ]:
 getInfobox(df[df['title']=='2014 FIFA World Cup']['text'].values[0])

"{{Infobox International Football Competition\n| tourney_name = FIFA World Cup\n| year = 2014\n| other_titles   = Copa do Mundo da FIFA<br />Brasil 2014{{refn|group=nb|The [[Portuguese language|Portuguese]] pronunciation is {{IPA-pt|ˈkɔpɐ du ˈmũdu dɐ ˈfifɐ bɾɐˈziw ˈdojz ˈmiw i kɐˈtoʁzi|}}, in Brazil's standard pronunciation.}}\n| image = Philipp Lahm lifts the 2014 FIFA World Cup.jpg\n| size = 250px\n| caption = Germany lifting the World Cup trophy.\n| country = Brazil\n| dates = 13 June – 13 July\n| confederations = 6\n| num_teams = 32\n| venues = 12\n| cities = 12\n| champion = Germany\n| count = 4\n| second = Argentina\n| third = Netherlands\n| fourth = Brazil\n| matches = 64\n| goals = 171\n| attendance = 3429873\n| top_scorer = {{flagicon|Colombia}} [[James Rodríguez]]<ref>{{cite web|url=http://www.bbc.com/sport/football/world-cup/top-scorers|title=Top Scorers - World Cup - Football|website=BBC Sport}}</ref><br>(6 goals)\n| prevseason = [[2010 FIFA World Cup|2010]]\n| nextseason =

In [ ]:
getInfobox(df[df['title']=='Qatar Stars League']['text'].values[0])

'{{Infobox football league\n|leaguename=Qatar Stars League\n|logo=\n|country=[[Qatar]]\n|confederation=[[AFC]]\n|founded=1963\n|folded=\n|level=1\n|divisions=\n|number of teams=12\n|promotion to=\n|relegation to=\n|domestic cup=\n|international cup=\n|current champions=[[Al-Gharafa S.C.|Al-Gharafa]]\n|season=2008/09\n|most successful club=[[Al-Sadd S.C.|Al-Sadd]] (12)\n|tv partners=\n|website=\n|current season=\n}}\n'

Ce texte suit un format défini par Wikipédia. Nous n'expliquerons pas tous les détailles, mais depuis la
deuxième ligne, chaque ligne est une attribut et sa valeur. Cette information corresponde à celle qu'on
trouve dans la boîte à droite de chaque page Wikipédia (voir
https://simple.wikipedia.org/wiki/2014_FIFA_World_Cup). Par exemple, dans notre script nous avons
trouvé le vainqueur pour l'année 2014 de la coupe du monde. Vous pouvez modifier le script pour obtenir des
autres informations.


In [ ]:
for line in str(df[df['title']=='2014 FIFA World Cup']['text'].values).split('\\n'):
    if "| champion" in line:
        print(line)

| champion = Germany


1) Vous êtes encouragé à développer une application pour sauvegarde toute l'information contenue
entre crochets **{{Infobox INFORMATION IMPORTANT }}**. L'information doit être sauvegardée en
utilisant des triples. Dans la web sémantique, un format hautement répondu est le Resource Description
Framework (RDF). En RDF, une triple est un association de sujet, prédicat et objet. Dans notre
exemple, **2014 FIFA World Cup **est le sujet, **champion** est le prédicat et **Germany** est l'objet. Ce
format est actuellement utilisé pour représenter de bases de connaissances de grande taille (Par
exemple, [YAGO](https://yago-knowledge.org/) est une base de connaissances qui possède 10 millions d'entités avec plus de 120
millions de triplets. Une autre base de connaisance est [DBpedia](https://wiki.dbpedia.org/).). L'information entre crochets peut contenir un ou plusieurs triplets.

In [ ]:
def retourTriplets(titre):
  """
  Take the title of a wikipedia's page from our DataFrame and return
  a list of triplets (subject,predicate,obejct) contained in the infobox's page
  
  """

    txt =  getInfobox(df[df['title']==titre]['text'].values[0])
    txt1 = txt.split('|')
    listenew = [element.replace("\n","") for element in txt1 if ('=' in element)]
    listeTriplets = list()
    for element in listenew :
        a,b = element.split("=", maxsplit = 1)
        listeTriplets.append((titre,a,b))
    return(listeTriplets)

In [ ]:
#test
print(retourTriplets('United States'))
test = retourTriplets('United States')

[('United States', ' conventional_long_name ', ' United States of America'), ('United States', ' common_name            ', ' the United States'), ('United States', ' image_flag                ', ' Flag of the United States.svg'), ('United States', ' flag_type                ', ' {{big'), ('United States', ' image_coat                ', ' Greater coat of arms of the United States.svg'), ('United States', ' symbol_type                ', ' {{big'), ('United States', ' national_motto         ', ' "[[In God We Trust]]"'), ('United States', ' national_anthem        ', ' "[[The Star-Spangled Banner]]" <center>[[File:"The Star-Spangled Banner" performed by the United States Navy Band.mp3]]<center>'), ('United States', ' march                  ', ' "[[The Stars and Stripes Forever]]" <center>[[File:March, "The Stars and Stripes Forever" · Colonel John R. Bourgeois, Director · John Philip Sousa · United States Marine Band.ogg]]<center>'), ('United States', ' other_symbol           ', ' <div styl

2) Exportez les triplets que vous avez trouvez en RDF/XML. Voici un exemple de comment créer une
base de connaissances dans ce format avec python.

Base de connaissances (wiki_example.rdf) :

```
<?xml version="1.0" encoding="UTF-8"?>
<rdf:RDF xmlns:ns1="http://xmlns.com/foaf/0.1/" xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#">
 <rdf:Description rdf:about="http://peter.me">
  <ns1:mbox>mailto:peter@peter.me</ns1:mbox>
  <ns1:name>Peter Goodguy</ns1:name>
 </rdf:Description>
 <rdf:Description rdf:about="http://carol.me">
  <ns1:mbox>mailto:carol@carol.me</ns1:mbox>
 </rdf:Description>
 <rdf:Description rdf:about="http://jlow.me">
  <ns1:name>Johnny Lee Outlaw</ns1:name>
  <ns1:mbox>mailto:jlow@jlow.me</ns1:mbox>
 </rdf:Description>
</rdf:RDF>
```
Qui contient l'information :

| Sujet             	| Pédricat  	| Objet                   	|
|-------------------	|-----------	|-------------------------	|
| <http://jlow.me>  	| foaf:name 	| Johnny Lee Outlaw       	|
| <http://jlow.me>  	| foaf:mbox 	| <mailto:jlow@jlow.me>   	|
| <http://peter.me> 	| foaf:name 	| Peter Goodguy           	|
| <http://peter.me> 	| foaf:mbox 	| <mailto:peter@peter.me> 	|
| <http://carol.me> 	| foaf:mbox 	| <mailto:carol@carol.me> 	|


Ci-dessous le code pour générer ce fichier:


In [ ]:
!pip install rdflib

     |████████████████████████████████| 235kB 4.8MB/s 
     |████████████████████████████████| 51kB 6.2MB/s 


In [ ]:
import rdflib
from rdflib.namespace import FOAF
from rdflib import Namespace
from rdflib import Graph, URIRef, BNode, Literal
myns =  Namespace("http://www.mynameespace.org/myNameSpaceSID#")

g = Graph()
johnny = URIRef('http://jlow.me')
peter = URIRef('http://peter.me')
carol = URIRef('http://carol.me')
g.add((johnny,FOAF.name,Literal('Johnny Lee Outlaw')))
g.add((johnny,FOAF.mbox,Literal('mailto:jlow@jlow.me')))
g.add((peter,FOAF.name,Literal('Peter Goodguy')))
g.add((peter,FOAF.mbox,Literal('mailto:peter@peter.me')))
g.add((johnny,myns["email"],Literal('mailto:jlow@jlow.me')))
g.serialize("wiki_example_generated.rdf")

In [ ]:
def titleToLink (title) :
  """
    Create a link with the title of the Wikipedia's page
  """
    title = title.replace(" ", "_")
    return 'https://simple.wikipedia.org/wiki/' + str(title)

In [ ]:
import rdflib
from rdflib.namespace import FOAF
from rdflib import Namespace
from rdflib import Graph, URIRef, BNode, Literal
myns =  Namespace("http://www.mynameespace.org/myNameSpaceSID#")

g = Graph()
for titre in df['title'][200:300] :
    titreActuel = retourTriplets(titre)
    for triplet in titreActuel :
        g.add((URIRef(titleToLink(triplet[0])),Literal(triplet[1]),Literal(triplet[2])))
# g.serialize("wiki_example_generated.rdf")
print(g.serialize(format = "turtle").decode('utf-8'))


3) Importez la base de connaissances pour faire de requêtes SPARQL (SPARQL Protocol and RDF
Query Language).
Voici l'exemple d'une requête SPARQL sur la basse de connaissances (query_example.rq) :

```
PREFIX foaf: <http://xmlns.com/foaf/0.1/> 
SELECT ?name ?mbox
WHERE
 { ?x foaf:name ?name.
 ?x foaf:mbox ?mbox }

 ```

 Utilisez le code ci-dessous pour exécuter la requête 

4) Créez une requête pour trouver le champion de la coupe du monde en 2014 et éxécutez-la sur la base de connaisance construite dans le point 2.


In [ ]:
#Pas réussi à sérializer et du coup à lancer ça

# g1 = rdflib.Graph()
# g1.parse("wiki_example_generated.rdf", format="xml")
# q = "PREFIX foaf: <http://www.mynameespace.org/myNameSpaceSID/> SELECT ?champion WHERE { ?x foaf:champion ?champion  }"
# x1 = g1.query(q)
# print(list(x1))

5) Créez une requête pour trouver les championnat où le meilleur buteur a été joueur du Valencia C.F.
et testez la requête avec la base de connaissances construite dans le point 2. Avez-vous une meilleur idée pour le faire ?
(par exemple sans utiliser SPARQL).

Réponse :

On peut faire comme dans les précédents TP en cherchant à l'aide d'un Pattern et/ou en relevant des phrases ayant "Valencia" "meilleur buteur" dans la phrase.